In [15]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly
import plotly.express as px
import warnings
warnings.filterwarnings("ignore")

plt.rcParams["figure.figsize"] = (20, 9)
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import os

In [37]:
from itertools import groupby, count

# get all the frames with blinks detected
def get_Binks(df:pd.DataFrame) -> list:
    num_blinks = []
    threshold = (max(df["EMA"]) + min(df["EAR"])) / 2
    #print("Threshold:",threshold)
    for i in range(df.shape[0]):
        if (df["EAR"].iloc[i] - df["EMA"].iloc[i]) < (threshold):
            num_blinks.append(i)
    
    return num_blinks

# NOTE: accumulate consecutive frames to get number of blinks
def accumulate_Blinks(blinks:list) -> list:
    groups = groupby(blinks, key=lambda item, c = count():item-next(c))
    final_list = [list(g) for k, g in groups]

    return final_list

# Count the number of elements in a range
def get_Count(list1, l, r):
    # Traversing the list with on line for loop
    # check if number is in range of not
    return sum( l <= x <= r for x in list1)

# NOTE: get the dictionary containing number of blinks every minute
def get_Frequency(df, result):
    freq_by_min = {}
    
    for i in df["MINUTE"].unique():
        df_tmp = df[df["MINUTE"] == i]
        freq_by_min[i] = get_Count(result, min(df_tmp["FN"]), max(df_tmp["FN"]))

    return freq_by_min


# NOTE: AMPLITUDE
def get_Amplitude(df, result):
    fn_2_amplitude = {}
    for i in result:
        fn_2_amplitude[i] = df["EAR"].iloc[i]
    
    return fn_2_amplitude

#! VELOCITY AND DURATION

# def get the frames of blink
def get_Blink_Frames(mid_frame:int, df:pd.DataFrame) -> tuple:
    start, end = mid_frame, mid_frame

    if start > 0:
        while abs(np.round(abs(df["EMA"].iloc[start]) - abs(df["EAR"].iloc[start]))) > 0:
            start -= 1
        
    if end < df.shape[0]:
        while abs(np.round(abs(df["EMA"].iloc[end]) - abs(df["EAR"].iloc[end]))) > 0:
            end += 1

    return (start+1, end + 1)

# def get the time difference
def get_Blink_Duration(mid_frame:int, df:pd.DataFrame) -> tuple:
    start, end = get_Blink_Frames(mid_frame, df)

    duration = (df["TIMESTAMP"].iloc[mid_frame] - df["TIMESTAMP"].iloc[start]) / 1000

    return duration, start, mid_frame, end

# # def get blink velocity in frames/sec
# def get_Blink_Velocity(duration:float, start:int, end:int) -> float:
#     velocity = (end - start) / duration

#     return velocity

# def get blink velocity in frames/sec
def get_Blink_Velocity(duration:float, start:int, mid:int, df:pd.DataFrame) -> float:

    EAR_S = abs(df["EAR"].iloc[start])
    EAR_M = abs(df["EAR"].iloc[mid])

    velocity = (EAR_M - EAR_S) / duration

    return velocity

# def get perclos index
def get_PERCLOS(duration_results:list, time_window:int = 60):
    TIME_INTERVAL = time_window
    PERCLOS = {}
    window = []

    for i in duration_results:
        if i[2] < TIME_INTERVAL:
            window.append((i[3] - i[1]))
        else:
            PERCLOS[TIME_INTERVAL] = window
            window = []
            TIME_INTERVAL += time_window

    return PERCLOS

# calculate perclos index
def calculate_PERCLOS(PERCLOS:dict, time_window:int = 60) -> list:
    p_index = []

    for i in PERCLOS.keys():
        p_index.append((np.sum(PERCLOS[i]) / time_window))
    
    return p_index


In [53]:
path = f"./rcam/"
csvfiles = []
number_of_blinks = []
for x in os.listdir(path):
    if x.endswith(".csv"):
            csvfiles.append(x)
    #print(videofilename)
csvfiles.sort()
counter = 1
perclos_value=list()
for x in csvfiles:
    df_alert = pd.read_csv(f"./rcam/{x}")
    if df_alert.empty:
        continue
    mean, std_dev = df_alert["EAR"].describe()[1], df_alert["EAR"].describe()[2]
    df_alert["EAR"] = df_alert["EAR"].apply(lambda x: (x - mean)/std_dev)
    df_alert["EMA"] = df_alert["EAR"].ewm(80).mean()
    df_alert["CMA"] = df_alert["EAR"].expanding().mean()
    df_alert["SMA"] = df_alert["EAR"].rolling(50, min_periods=1).mean()
    df_alert["EMA_MEAN"] = [df_alert["EMA"].mean()] * df_alert.shape[0]
    num_blinks = []
    threshold = (max(df_alert["EMA"]) + min(df_alert["EAR"])) / 2
    #print("Threash hold: ",threshold)
    result_alert_full = accumulate_Blinks(get_Binks(df_alert))
    num_blinks = len(result_alert_full)
    print(f"Total number of blinks detected are = {num_blinks}.")

    result_alert = [int(np.floor(np.mean(i))) for i in result_alert_full]

    #p1_0_freq = get_Frequency(df_alert, result_alert)

    #print(p1_0_freq)
    #print("Number of blinks",num_of_blinks)

    #plt.figure()
    #sns.lineplot(data= df_alert[["FN","EAR"]], x="FN",y="EAR")

    '''fig = make_subplots(rows=1, cols=1)


    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = df_alert["EAR"],  name = "EAR", mode = "lines"),
        row=1, col=1
    )
    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = df_alert["EMA"],  name = "EMA", mode = "lines"),
        row=1, col=1
    )
    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = [np.mean(df_alert["EMA"])] * df_alert.shape[0],  name = "EMA_MEAN", mode = "lines"),
        row=1, col=1
    )
    fig.update_layout(height=450, width=1550, title_text="EAR with EMA: "+ x + "       Number of blinks: "+ str(num_of_blinks))
    fig.show()

print(number_of_blinks)'''

Total number of blinks detected are = 19.
Total number of blinks detected are = 11.
Total number of blinks detected are = 9.
Total number of blinks detected are = 12.
Total number of blinks detected are = 13.
Total number of blinks detected are = 7.
Total number of blinks detected are = 13.
Total number of blinks detected are = 36.
Total number of blinks detected are = 21.
Total number of blinks detected are = 7.
Total number of blinks detected are = 5.
Total number of blinks detected are = 22.
Total number of blinks detected are = 24.
Total number of blinks detected are = 16.
Total number of blinks detected are = 12.
Total number of blinks detected are = 8.
Total number of blinks detected are = 20.
Total number of blinks detected are = 32.
Total number of blinks detected are = 19.
Total number of blinks detected are = 18.
Total number of blinks detected are = 9.
Total number of blinks detected are = 21.
Total number of blinks detected are = 36.
Total number of blinks detected are = 12

In [110]:
from tokenize import Name


path = f"./rcam/"
csvfiles = []
number_of_blinks = []
for x in os.listdir(path):
    if x.endswith(".csv"):
            csvfiles.append(x)
    #print(videofilename)
csvfiles.sort()
counter = 1
duration_frames = []
perclos_value=list()
for x in csvfiles:
    df_alert = pd.read_csv(f"./rcam/{x}")
    if df_alert.empty:
        continue
    mean, std_dev = df_alert["EAR"].describe()[1], df_alert["EAR"].describe()[2]
    df_alert["EMA"] = df_alert["EAR"].ewm(4).mean()
    startframe = endframe =0
    num_blinks = []
    counter = num_of_blinks= 0
    for i in range(df_alert.shape[0]):
        #if (df["EAR"].iloc(i)) < (threshold):
        if (df_alert["EAR"].iloc[i]) < (df_alert["EMA"].iloc[i-1]):
            num_blinks.append(i)
            counter += 1 
        else:
            if counter > 7:
                duration_frames.append(df_alert["FN"].iloc[i]-8)
                duration_frames.append(df_alert["FN"].iloc[i])
                num_of_blinks += 1
    #df_alert.dropna(inplace=True)
            counter = 0
    number_of_blinks.append(num_of_blinks)
    #print("Number of blinks",num_of_blinks)

    #plt.figure()
    #sns.lineplot(data= df_alert[["FN","EAR"]], x="FN",y="EAR")
    print("Frame number when EAR is less than threshold for the video: ", x)
    print(duration_frames)
    nparray_duration_frame = np.array(duration_frames)
    result = nparray_duration_frame/20
    print(result.tolist())
    duration_frames.clear()
    '''fig = make_subplots(rows=1, cols=1)


    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = df_alert["EAR"],  name = "EAR", mode = "lines"),
        row=1, col=1
    )
    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = df_alert["EMA"],  name = "EMA", mode = "lines"),
        row=1, col=1
    )
    fig.append_trace(
        go.Scatter(x = df_alert["FN"], y = [np.mean(df_alert["EMA"])] * df_alert.shape[0],  name = "EMA_MEAN", mode = "lines"),
        row=1, col=1
    )
    fig.update_layout(height=450, width=1550, title_text="EAR with EMA: "+ x + "       Number of blinks: "+ str(num_of_blinks))
    fig.show()
'''
print(number_of_blinks)

Frame number when EAR is less than threshold for the video:  rcam_10_EAR.csv
[60, 68, 134, 142, 370, 378, 395, 403, 569, 577, 732, 740, 777, 785, 895, 903, 923, 931, 1040, 1048, 1181, 1189]
[3.0, 3.4, 6.7, 7.1, 18.5, 18.9, 19.75, 20.15, 28.45, 28.85, 36.6, 37.0, 38.85, 39.25, 44.75, 45.15, 46.15, 46.55, 52.0, 52.4, 59.05, 59.45]


Frame number when EAR is less than threshold for the video:  rcam_11_EAR.csv
[19, 27, 77, 85, 298, 306, 488, 496, 621, 629, 640, 648, 760, 768, 951, 959, 985, 993, 1073, 1081]
[0.95, 1.35, 3.85, 4.25, 14.9, 15.3, 24.4, 24.8, 31.05, 31.45, 32.0, 32.4, 38.0, 38.4, 47.55, 47.95, 49.25, 49.65, 53.65, 54.05]


Frame number when EAR is less than threshold for the video:  rcam_220903_131827_EAR.csv
[28, 36, 598, 606, 1169, 1177, 1188, 1196]
[1.4, 1.8, 29.9, 30.3, 58.45, 58.85, 59.4, 59.8]


Frame number when EAR is less than threshold for the video:  rcam_220903_131908_EAR.csv
[49, 57, 145, 153, 280, 288, 356, 364, 399, 407, 513, 521, 694, 702, 715, 723, 837, 845, 878, 886, 897, 905, 993, 1001, 1015, 1023, 1041, 1049, 1119, 1127]
[2.45, 2.85, 7.25, 7.65, 14.0, 14.4, 17.8, 18.2, 19.95, 20.35, 25.65, 26.05, 34.7, 35.1, 35.75, 36.15, 41.85, 42.25, 43.9, 44.3, 44.85, 45.25, 49.65, 50.05, 50.75, 51.15, 52.05, 52.45, 55.95, 56.35]


Frame number when EAR is less than threshold for the video:  rcam_220903_131948_EAR.csv
[338, 346, 415, 423, 435, 443, 600, 608, 669, 677, 880, 888, 913, 921, 1025, 1033, 1115, 1123, 1167, 1175]
[16.9, 17.3, 20.75, 21.15, 21.75, 22.15, 30.0, 30.4, 33.45, 33.85, 44.0, 44.4, 45.65, 46.05, 51.25, 51.65, 55.75, 56.15, 58.35, 58.75]


...

Frame number when EAR is less than threshold for the video:  rcam_220903_133232_EAR.csv
[53, 61, 160, 168, 253, 261, 446, 454, 484, 492, 689, 697, 710, 718, 910, 918, 1006, 1014, 1021, 1029, 1057, 1065, 1107, 1115]
[2.65, 3.05, 8.0, 8.4, 12.65, 13.05, 22.3, 22.7, 24.2, 24.6, 34.45, 34.85, 35.5, 35.9, 45.5, 45.9, 50.3, 50.7, 51.05, 51.45, 52.85, 53.25, 55.35, 55.75]


Frame number when EAR is less than threshold for the video:  rcam_220903_133313_EAR.csv
[24, 32, 227, 235, 268, 276, 306, 314, 339, 347, 373, 381, 386, 394, 448, 456, 642, 650, 1186, 1194]
[1.2, 1.6, 11.35, 11.75, 13.4, 13.8, 15.3, 15.7, 16.95, 17.35, 18.65, 19.05, 19.3, 19.7, 22.4, 22.8, 32.1, 32.5, 59.3, 59.7]


Frame number when EAR is less than threshold for the video:  rcam_220903_133354_EAR.csv
[5, 13, 30, 38, 46, 54, 83, 91, 200, 208, 437, 445, 488, 496, 543, 551, 688, 696, 895, 903, 917, 925, 975, 983, 1116, 1124, 1131, 1139]
[0.25, 0.65, 1.5, 1.9, 2.3, 2.7, 4.15, 4.55, 10.0, 10.4, 21.85, 22.25, 24.4, 24.8, 27.15, 27.55, 34.4, 34.8, 44.75, 45.15, 45.85, 46.25, 48.75, 49.15, 55.8, 56.2, 56.55, 56.95]


Frame number when EAR is less than threshold for the video:  rcam_220903_133434_EAR.csv
[1, 9, 74, 82, 162, 170, 196, 204, 220, 228, 321, 329, 359, 367, 429, 437, 439, 447]
[0.05, 0.45, 3.7, 4.1, 8.1, 8.5, 9.8, 10.2, 11.0, 11.4, 16.05, 16.45, 17.95, 18.35, 21.45, 21.85, 21.95, 22.35]


[11, 10, 4, 15, 10, 15, 18, 12, 16, 11, 10, 11, 18, 19, 12, 11, 13, 21, 16, 11, 8, 15, 12, 12, 10, 14, 9]


In [92]:
df_alert[["EAR","EMA"]].head(50)

EAR       EMA
0   0.246055  0.246055
1   0.200586  0.220794
2   0.178276  0.203369
3   0.187027  0.197833
4   0.149060  0.183324
5   0.138974  0.171303
6   0.149689  0.165833
7   0.137469  0.159016
8   0.199607  0.168393
9   0.231813  0.182603
10  0.282146  0.204382
11  0.275957  0.219754
12  0.269070  0.230191
13  0.252010  0.234755
14  0.269906  0.242042
15  0.260682  0.245878
16  0.283823  0.253642
17  0.276577  0.258313
18  0.298217  0.266410
19  0.300964  0.273402
20  0.295281  0.277818
21  0.273806  0.277010
22  0.298867  0.281407
23  0.274527  0.280025
24  0.309407  0.285923
25  0.314140  0.291584
26  0.308012  0.294877
27  0.301714  0.296247
28  0.305052  0.298011
29  0.276312  0.293666
30  0.237585  0.282439
31  0.178789  0.261692
32  0.318327  0.273026
33  0.301682  0.278760
34  0.348850  0.292784
35  0.405687  0.315372
36  0.432669  0.338837
37  0.472109  0.365497
38  0.561635  0.404731
39  0.437382  0.411262
40  0.535539  0.436120
41  0.441010  0.437098
42  0.368859  0.423450
43  0.307317  0.400222
44  0.331372  0.386451
45  0.396566  0.388474
46  0.308493  0.372478
47  0.359485  0.369879
48  0.283110  0.352525
49  0.323046  0.346629